In [33]:
import requests
import pandas as pd
import json
import mysql.connector as mysql
from sqlalchemy import create_engine
import hashlib

In [34]:
response = requests.get("http://universities.hipolabs.com/search?country")

text = response.json()
text = json.dumps(text);

#json text to python dict

data = json.loads(text)

data

[{'domains': ['mbzuai.ac.ae'],
  'country': 'United Arab Emirates',
  'web_pages': ['https://mbzuai.ac.ae/'],
  'name': 'Mohamed bin Zayed University of Artificial Intelligence (MBZUAI)',
  'alpha_two_code': 'AE',
  'state-province': 'Abu Dhabi'},
 {'domains': ['sempreceub.com', 'uniceub.br'],
  'country': 'Brazil',
  'web_pages': ['https://www.uniceub.br'],
  'name': 'Centro Universitário de Brasília, UNICEUB',
  'alpha_two_code': 'BR',
  'state-province': None},
 {'domains': ['student.karazin.ua', 'karazin.ua'],
  'country': 'Ukraine',
  'web_pages': ['https://karazin.ua'],
  'name': 'Kharkiv National University',
  'alpha_two_code': 'UA',
  'state-province': None},
 {'domains': ['usm.cl'],
  'country': 'Chile',
  'web_pages': ['https://usm.cl'],
  'name': 'Universidad Técnica Federico Santa María',
  'alpha_two_code': 'CL',
  'state-province': None},
 {'domains': ['ieseg.fr'],
  'country': 'France',
  'web_pages': ['https://ieseg.fr'],
  'name': 'IÉSEG School of Management',
  'alph

In [35]:

list_of_header = []

for val in data:
    for key in val:
        list_of_header.append(key)
    break;

print(list_of_header)

connection = mysql.connect(user='root', 
                           password='softzino',
                           host='127.0.0.1',
                           database='new_schema')
connection.is_connected()

['domains', 'country', 'web_pages', 'name', 'alpha_two_code', 'state-province']


True

In [36]:
def my_hashing(string):

    string = bytes(string, 'utf-8')
    
    sha256 = hashlib.sha256()

    sha256.update(string)
    
    string_hash = sha256.hexdigest()
     
    return string_hash

In [37]:

list_of_values = []

for val in data:
    mylist = []
    my_string = ""
    for key in val:
        mylist.append(val[key])

        fval = val[key]

        if(type(fval) == type([])):
            fval = json.dumps(fval)
            
        fval = connection._cmysql.escape_string(str(fval))
        fval = fval.decode('utf-8')

        my_string += fval
        
    #print(my_string)
    hash_value = my_hashing(my_string) 
    #print(hash_value)
    
    mylist.append(str(hash_value))
    print(mylist)
    
    list_of_values.append(mylist)

print(list_of_values)

[['mbzuai.ac.ae'], 'United Arab Emirates', ['https://mbzuai.ac.ae/'], 'Mohamed bin Zayed University of Artificial Intelligence (MBZUAI)', 'AE', 'Abu Dhabi', '7600eb5538ed2a86fb2edd1c1e31fafcc80d92ea242a7416bf8ff139b78d1cfe']
[['sempreceub.com', 'uniceub.br'], 'Brazil', ['https://www.uniceub.br'], 'Centro Universitário de Brasília, UNICEUB', 'BR', None, '8245ad689ae0030778a7edd65817c46c095d1c33dd6c55a93626dabbe5580b06']
[['student.karazin.ua', 'karazin.ua'], 'Ukraine', ['https://karazin.ua'], 'Kharkiv National University', 'UA', None, '56a8be022f2d8c74c87f016466ce20ded3e4757ee17e99e308425b740590acd9']
[['usm.cl'], 'Chile', ['https://usm.cl'], 'Universidad Técnica Federico Santa María', 'CL', None, '4e69ade241ee488c503e2b74da13ed0873b2cd95c0eb90f3f8f56a7db31e79bb']
[['ieseg.fr'], 'France', ['https://ieseg.fr'], 'IÉSEG School of Management', 'FR', None, '174848b8f66f9c0415392b5d83ed41928dc6104415869f37576dd1cd0d513ec2']
[['mail2.sysu.edu.cn', 'mail.sysu.edu.cn'], 'China', ['https://sysu.e

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [38]:
def creating_table(table_name):

        cursor = connection.cursor()
    
        query = f"CREATE TABLE IF NOT EXISTS {table_name} (alpha_two_code varchar(255), state_province varchar(255), domains varchar(255), name varchar(255), web_pages varchar(255), country varchar(255), hash_value varchar(255), created_date datetime, updated_date datetime)"
    
        print(query)
    
        cursor.execute(query)
        connection.commit()
        
            
        print(f"Successfuly create table {table_name}")   
    
creating_table("All_uni")

CREATE TABLE IF NOT EXISTS All_uni (alpha_two_code varchar(255), state_province varchar(255), domains varchar(255), name varchar(255), web_pages varchar(255), country varchar(255), hash_value varchar(255), created_date datetime, updated_date datetime)
Successfuly create table All_uni


In [39]:
from datetime import datetime

now = datetime.now()
print(now)

2024-02-23 15:44:28.971343


In [40]:
def inserting_data(list_of_list):

    cursor = connection.cursor()
    
    for val in list_of_list:
         
        query_text = "("
        
        for index, fval in enumerate(val):
    
            
            if(type(fval) == type([])):
                fval = json.dumps(fval)

            fval = connection._cmysql.escape_string(str(fval))
            fval = fval.decode('utf-8')

            query_text += f"'{fval}',"

        query_text += f"'{datetime.now()}', '{datetime.now()}'"
            
        query_text += ")"

        main_query = f"INSERT INTO All_uni VALUES {query_text}"
        print(main_query)

        cursor.execute(main_query)
        connection.commit()


inserting_data(list_of_values)

INSERT INTO All_uni VALUES ('[\"mbzuai.ac.ae\"]','United Arab Emirates','[\"https://mbzuai.ac.ae/\"]','Mohamed bin Zayed University of Artificial Intelligence (MBZUAI)','AE','Abu Dhabi','7600eb5538ed2a86fb2edd1c1e31fafcc80d92ea242a7416bf8ff139b78d1cfe','2024-02-23 15:44:28.986017', '2024-02-23 15:44:28.986035')
INSERT INTO All_uni VALUES ('[\"sempreceub.com\", \"uniceub.br\"]','Brazil','[\"https://www.uniceub.br\"]','Centro Universitário de Brasília, UNICEUB','BR','None','8245ad689ae0030778a7edd65817c46c095d1c33dd6c55a93626dabbe5580b06','2024-02-23 15:44:28.990561', '2024-02-23 15:44:28.990582')
INSERT INTO All_uni VALUES ('[\"student.karazin.ua\", \"karazin.ua\"]','Ukraine','[\"https://karazin.ua\"]','Kharkiv National University','UA','None','56a8be022f2d8c74c87f016466ce20ded3e4757ee17e99e308425b740590acd9','2024-02-23 15:44:28.993602', '2024-02-23 15:44:28.993622')
INSERT INTO All_uni VALUES ('[\"usm.cl\"]','Chile','[\"https://usm.cl\"]','Universidad Técnica Federico Santa María','CL

In [41]:
response = requests.get("http://universities.hipolabs.com/search?country")

text = response.json()
text = json.dumps(text);

#json text to python dict

data = json.loads(text)

data

[{'domains': ['mbzuai.ac.ae'],
  'country': 'United Arab Emirates',
  'web_pages': ['https://mbzuai.ac.ae/'],
  'name': 'Mohamed bin Zayed University of Artificial Intelligence (MBZUAI)',
  'alpha_two_code': 'AE',
  'state-province': 'Abu Dhabi'},
 {'domains': ['sempreceub.com', 'uniceub.br'],
  'country': 'Brazil',
  'web_pages': ['https://www.uniceub.br'],
  'name': 'Centro Universitário de Brasília, UNICEUB',
  'alpha_two_code': 'BR',
  'state-province': None},
 {'domains': ['student.karazin.ua', 'karazin.ua'],
  'country': 'Ukraine',
  'web_pages': ['https://karazin.ua'],
  'name': 'Kharkiv National University',
  'alpha_two_code': 'UA',
  'state-province': None},
 {'domains': ['usm.cl'],
  'country': 'Chile',
  'web_pages': ['https://usm.cl'],
  'name': 'Universidad Técnica Federico Santa María',
  'alpha_two_code': 'CL',
  'state-province': None},
 {'domains': ['ieseg.fr'],
  'country': 'France',
  'web_pages': ['https://ieseg.fr'],
  'name': 'IÉSEG School of Management',
  'alph

In [42]:
connection = mysql.connect(user='root', 
                           password='softzino',
                           host='127.0.0.1',
                           database='new_schema')
connection.is_connected()

True

In [ ]:
list_of_values = []

for val in data:
    mylist = []
    my_string = ""
    for key in val:
        mylist.append(val[key])

        fval = val[key]

        if(type(fval) == type([])):
            fval = json.dumps(fval)
            
        fval = connection._cmysql.escape_string(str(fval))
        fval = fval.decode('utf-8')

        my_string += fval
        
    #print(my_string)
    hash_value = my_hashing(my_string) 
    
    mylist.append(str(hash_value))
    
    list_of_values.append(mylist)

print(list_of_values)

In [ ]:
def update_rows(list_of_val):

    cursor = connection.cursor()
    
    for val in list_of_val:
        my_uni_name = val[3]
        my_hash = val[6]

        my_uni_name = connection._cmysql.escape_string(str(my_uni_name))
        my_uni_name = my_uni_name.decode('utf-8')

        #print(my_uni_name, my_hash)

        query_text = f"select name, hash_value from All_uni where name = '{my_uni_name}'"

        cursor.execute(query_text)
        
        query_output = cursor.fetchall()
        
        found_hash_val = query_output[0][1]

        print(my_hash, found_hash_val)

        if found_hash_val != my_hash:
            print("Not ok")
        
        break
        

update_rows(list_of_values)